# DBSCAN

In this notebook you will use GPU-accelerated DBSCAN to identify clusters of infected people.

## Objectives

By the time you complete this notebook you will be able to:

- Use GPU-accelerated DBSCAN
- Use cuXfilter to visualize DBSCAN clusters

## Imports

In [1]:
import cudf
import cuml

import cuxfilter as cxf

## Load Data

For this notebook, we again load a subset of our population data with only the columns we need. An `infected` column has been added to the data to indicate whether or not a person is known to be infected with our simulated virus.

In [15]:
gdf = cudf.read_csv('./data/pop_2-04.csv', dtype=['float32', 'float32', 'float32'])
print(gdf.dtypes)
gdf.shape

northing    float32
easting     float32
infected    float32
dtype: object


(1000000, 3)

In [16]:
gdf

northing       easting  infected
0       178547.296875  368012.12500       0.0
1       174068.281250  543802.12500       0.0
2       358293.687500  435639.87500       0.0
3        87240.304688  389607.37500       0.0
4       158261.015625  340764.93750       0.0
...               ...           ...       ...
999995  116619.835938  569043.75000       0.0
999996  113994.406250  441655.40625       0.0
999997  400215.156250  362622.31250       0.0
999998  152768.046875  613543.12500       0.0
999999   91709.460938  579722.87500       1.0

[1000000 rows x 3 columns]

In [21]:
gdf['infected'].value_counts()

1.0    15669
Name: infected, dtype: int32

## DBSCAN Clustering

DBSCAN is another unsupervised clustering algorithm that is particularly effective when the number of clusters is not known up front and the clusters may have concave or other unusual shapes--a situation that often applies in geospatial analytics.

In this series of exercises you will use DBSCAN to identify clusters of infected people by location, which may help us identify groups becoming infected from common patient zeroes and assist in response planning.

## Exercise: Make a DBSCAN Instance

Create a DBSCAN instance by using `cuml.DBSCAN`. Pass in the named argument `eps` (the maximum distance a point can be from the nearest point in a cluster to be considered possibly in that cluster) to be `5000`. Since the `northing` and `easting` values we created are measured in meters, this will allow us to identify clusters of infected people where individuals may be separated from the rest of the cluster by up to 5 kilometers.

#### Solution

In [18]:
# %load solutions/dbscan_instance
dbscan = cuml.DBSCAN(eps=5000)


### Exercise: Identify Infected Clusters

Create a new dataframe from rows of the original dataframe where `infected` is `1` (true), and call it `infected_df`--be sure to reset the dataframe's index afterward. Use `dbscan.fit_predict` to perform clustering on the `northing` and `easting` columns of `infected_df`, and turn the resulting series into a new column in `infected_gdf` called "cluster". Finally, compute the number of clusters identified by DBSCAN.

#### Solution

In [19]:
gdf = gdf[gdf['infected'] == 1].reset_index()
gdf['cluster'] = dbscan.fit_predict(gdf[['northing', 'easting']])
gdf['cluster'].nunique()


96

In [20]:
gdf

index       northing       easting  infected  cluster
0          41  595509.250000  426545.59375       1.0       -1
1         182  185086.609375  547718.00000       1.0        0
2         190  183406.546875  528708.06250       1.0        0
3         216  373846.562500  485603.84375       1.0        0
4         266  194947.406250  535378.37500       1.0        0
...       ...            ...           ...       ...      ...
15664  999847  321325.937500  401268.15625       1.0        0
15665  999947  181178.015625  526044.25000       1.0        0
15666  999963  236423.734375  602746.68750       1.0        0
15667  999979  186677.390625  517625.53125       1.0        0
15668  999999   91709.460938  579722.87500       1.0       -1

[15669 rows x 5 columns]

## Visualize the Clusters

Because we have the same column names as in the K-means example--`easting`, `northing`, and `cluster`--we can use the same code to visualize the clusters.

In [22]:
from pyproj import Transformer


trans = Transformer.from_crs('epsg:27700', 'epsg:3857')
gdf['x'], gdf['y'] = trans.transform(gdf['easting'].values_host, gdf['northing'].values_host)

### Associate a Data Source with cuXfilter

In [23]:
cxf_data = cxf.DataFrame.from_dataframe(gdf)

### Define Charts and Widgets

As in the K-means notebook, we have an existing integer column to use with multi-select: `cluster`.

In [24]:
import seaborn as sns


chart_width = 600
palet = [ "#1fe066", "#3182bd", "#f5641b", "#bd31a8", "#f2ff3d", "#000ba3"]
scatter_chart = cxf.charts.datashader.scatter(x='x', y='y', 
                                              width=chart_width, tile_provider="CartoLight", 
                                              aggregate_col='cluster', aggregate_fn='mean',
                                              height=int((gdf['northing'].max() - gdf['northing'].min()) / 
                                                         (gdf['easting'].max() - gdf['easting'].min()) *
                                                          chart_width),  color_palette = palet, 
                                              title = 'Infected people cluster')

scatter_chart_2 = cxf.charts.datashader.scatter(x='x', y='y', 
                                              width=chart_width, 
                                              aggregate_fn='count',
                                              height=int((gdf['northing'].max() - gdf['northing'].min()) / 
                                                         (gdf['easting'].max() - gdf['easting'].min()) *
                                                          chart_width), 
                                              title = 'Infected people density')
# color_palette = palet # НЕ ПОНЯЛ НИЧЕГО ЧЕ НЕ РАБОТАЕТ 
cluster_widget = cxf.charts.panel_widgets.multi_select('cluster')
charts_list = [scatter_chart, scatter_chart_2]

### Create and Show the Dashboard

In [25]:
dash = cxf_data.dashboard(charts_list, layout_array=[[1, 2]], sidebar=[cluster_widget], theme=cxf.themes.dark)

In [29]:
dash.app()

Row(sizing_mode='stretch_both')
    [0] Column(sizing_mode='stretch_height', width=280)
        [0] Card(collapsible=False, header_css_classes=['card-header', ...], sizing_mode='scale_width', title='Datapoints Selected')
            [0] Column(sizing_mode='stretch_both')
                [0] Number(css_classes=['indicator'], font_size='18pt', format='{value:,}', sizing_mode='stretch_width', value=15669)
                [1] Progress(sizing_mode='stretch_width', value=100)
        [1] Card(collapsible=False, header_css_classes=['card-header', ...], sizing_mode='scale_width', title='cluster_multi_select', width=400)
            [0] MultiSelect(height=200, options=[-1, 0, 1, 2, ...], sizing_mode='stretch_both', value=[''], width=400)
    [1] GridStack(allow_drag=False, allow_resize=False, ncols=11, nrows=6, sizing_mode='stretch_both')
        [0] Card(sizing_mode='stretch_both', title='Infected people cluster', width=600)
            [0] HoloViews(DynamicMap, height=400, sizing_mode='stretch_both')
        [1] Card(sizing_mode='stretch_both', title='Infected people density', width=600)
            [0] HoloViews(DynamicMap, height=400, sizing_mode='stretch_both')

In [27]:
scatter_chart.view()

Card(sizing_mode='scale_width', title='Infected people cluster', width=600)
    [0] HoloViews(DynamicMap, height=400, sizing_mode='stretch_both')

In [26]:
scatter_chart_2.view()

Card(sizing_mode='scale_width', title='Infected people density', width=600)
    [0] HoloViews(DynamicMap, height=400, sizing_mode='stretch_both')

In [10]:
%%js
var host = window.location.host;
element.innerText = "'http://"+host+"'";

<IPython.core.display.Javascript object>

Set `my_url` in the next cell to the value just printed, making sure to include the quotes:

In [11]:
my_url = 'http://ec2-54-208-137-113.compute-1.amazonaws.com'
dash.show(my_url, port=8789)

Dashboard running at port 8789


Row(sizing_mode='stretch_both')
    [0] Button(button_type='success', name='open cuxfilter d..., sizing_mode='stretch_both')

... and you can run the next cell to generate a link to the dashboard:

In [12]:
%%js
var host = window.location.host;
var url = 'http://'+host+'/lab/proxy/8789/';
element.innerHTML = '<a style="color:blue;" target="_blank" href='+url+'>Open Dashboard</a>';

<IPython.core.display.Javascript object>

In [50]:
dash.stop()

AttributeError: 'NoneType' object has no attribute '_stopped'

<br>
<div align="center"><h2>Please Restart the Kernel</h2></div>

In [ ]:
import IPython
app = IPython.Application.instance()
app.kernel.do_shutdown(True)

## Next

In the next notebook, you will use GPU-accelerated logistic regression to estimate infection risk based on features of our population members.